In [1]:
import plotly.graph_objects as go
from plotly.colors import n_colors
import numpy as np
import pandas as pd
import warnings
warnings.filterwarnings('ignore')

file = 'PAM194_Keratino_CytoPanel_1\pam194ObjAllcyto'
df = pd.read_pickle(file+'.pkl')

In [2]:
def generate_violins(data, col, name=None, sd=None):
    colors = n_colors('rgb(5, 200, 200)', 'rgb(200, 10, 10)', len(data), colortype='rgb')

    fig = go.Figure()
    for data_line, color in zip(data.keys(), colors):
        x = data[data_line][col]
            
        fig.add_trace(go.Violin(x=x, line_color=color, 
                                name=data_line))
        if sd is not None:
            m = np.mean(x)
            std = np.std(x)
            l = m-sd*std
            r = m+sd*std
            if r <= max(x):
                fig.add_vline(x=r, line_dash="dash", line_color=color)
            if l >= min(x):
                fig.add_vline(x=l, line_dash="dash", line_color=color)
    annotation = ' (' + str(sd)+' sds away)' if sd else ''
    fig.update_traces(orientation='h', side='positive', 
                      width=3, points='outliers')
    fig.update_layout(xaxis_showgrid=False, xaxis_zeroline=False, title = col + annotation)
    # fig.add_vrect(x0=0.9, x1=2)
    fig.add_vline(x=0, line_width=3, line_dash="dash", line_color="green")
    fig.show()
    # fig.write_image(name+".png")

In [3]:
def well_ttest(data, cytokine, dose, col, sd):
    name = cytokine + ' ' + str(dose)
    subset = data[name]
    wells = subset['Metadata_Well'].unique()
    subdata = {}
    for well in wells:
        subdata[name + ' ' + well] = subset[subset['Metadata_Well']==well]

    generate_violins(subdata, col, name, sd)

In [4]:
cd = df.groupby(by=['Metadata_Metadata_Cytokine', 'Metadata_Metadata_Dose']).mean().index

In [5]:
# group data by cytokines and doses
# put into dict data

data = {}
for i in cd:
    c = i[0]
    d = i[1]
    name = c + ' ' + str(d)
    data[name] = df[df['Metadata_Metadata_Cytokine']==c][df['Metadata_Metadata_Dose']==d]

In [6]:
# df.filter(regex = 'RadialDistribution_ZernikeMagnitude')

## Make t-tests between wells with different variables/columns

In [7]:
col = 'RadialDistribution_ZernikeMagnitude_CorrActin_0_0'

In [8]:
# perform t-tests by specifying cytokine and dosage of interest
# also showing the data points that fall out of some standard deviations

well_ttest(data, 'EGF', 33, col, 3)

In [9]:
# generate general violin plots across whole dataset

generate_violins(data, col, col)

### to look at distributions of variables under one same group for cytokine and dosage of interest

In [10]:
tmp_c = cd[2][0]
tmp_d = cd[2][1]
tmp = df[df['Metadata_Metadata_Cytokine']==tmp_c][df['Metadata_Metadata_Dose']==tmp_d]
tmp_gran = tmp.filter(regex = 'Gran')

In [11]:
colors = n_colors('rgb(5, 200, 200)', 'rgb(200, 10, 10)', len(data), colortype='rgb')

fig = go.Figure()
# i = 0
for i, color in zip(range(tmp_gran.shape[1]), colors):
    fig.add_trace(go.Violin(x=tmp_gran.iloc[:,i], line_color=color, name=tmp_gran.iloc[:,i].name))
    # i += 1

fig.update_traces(orientation='h', side='positive', width=3, points='outliers')
fig.update_layout(xaxis_showgrid=False, xaxis_zeroline=False, title = tmp_c+' '+str(tmp_d))
    # fig.add_vrect(x0=0.9, x1=2)
fig.add_vline(x=0, line_width=3, line_dash="dash", line_color="green")
fig.show()

### the following codes is provided by dash about selection of vlines shows, could be useful in displaying differnt number of standard deviations

In [12]:
# from dash import Dash, dcc, html, Input, Output
# import plotly.express as px

# app = Dash(__name__)


# app.layout = html.Div([
#     html.H4('Iris plot an interactive horizontal line'),
#     html.P("↓↓↓ try downloading the plot ↓↓↓", style={"text-align": "right", "font-weight": "bold"}),
#     dcc.Graph(id="graph"),
#     html.P("Position of hline"),
#     dcc.Slider(
#         id='slider-position', 
#         min=1, max=7, value=2.5, step=0.1,
#         marks={1: '1', 7: '7'}
#     )
# ])


# @app.callback(
#     Output("graph", "figure"), 
#     Input("slider-position", "value"))
# def display_graph(pos_x):
#     df = px.data.iris() # replace with your own data source
#     fig = px.scatter(
#         df, x="petal_length", y="petal_width")
#     fig.add_vline(
#         x=pos_x, line_width=3, line_dash="dash", 
#         line_color="green")
#     fig.add_hrect(
#         y0=0.9, y1=2.6, line_width=0, 
#         fillcolor="red", opacity=0.2)
#     return fig


# app.run_server(debug=True)